In [1]:
import os
import math
import random
from collections import defaultdict

from tqdm import tqdm
import numpy as np
import pandas as pd

import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader

from models.SASRec import SASRec

def set_seed(seed):
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    torch.cuda.manual_seed_all(seed)  # if use multi-GPU
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False
    np.random.seed(seed)
    random.seed(seed)    
    
seed=42
set_seed(seed)

class Config():
    def __init__(self):
        self.data_path    = 'data/train/'
        self.model_path   = './saved_model'
        self.model_name   = 'SASRec_1.pt'
        self.device       = 'cuda' if torch.cuda.is_available() else 'cpu'
        self.num_workers  = 4
        self.num_epochs   = 10
        self.batch_size   = 128
        self.lr           = 1e-3
        self.dropout_rate = 0.5
        self.max_len      = 50
        self.hidden_units = 50
        self.num_heads    = 1
        self.num_layers   = 2
        
config = Config()

#### load data

In [2]:
def get_path(path, base_path='data/train/'):
    return base_path + path

base_path     = 'data/train/'
rating_path   = get_path('train_ratings.csv')
director_path = get_path('directors.tsv')
genre_path    = get_path('genres.tsv')
title_path    = get_path('titles.tsv')
writer_path   = get_path('writers.tsv')
year_path     = get_path('years.tsv')

df = pd.read_csv(rating_path)
df.head()

user  item        time
0    11  4643  1230782529
1    11   170  1230782534
2    11   531  1230782539
3    11   616  1230782542
4    11  2140  1230782563

#### dataset

In [3]:
from time import time
class CustomDataset(Dataset):
    def __init__(self, config):
        path = config.data_path + 'train_ratings.csv'
        self.df = pd.read_csv(path)
        self.num_item, self.num_user, self.item2idx, self.user2idx = self._preprocess()
        self.idx2item, self.idx2user = {v: k for k, v in self.item2idx.items()}, {v: k for k, v in self.user2idx.items()}
        self.user_train, self.user_valid = self._split()
        self.max_len = config.max_len

    def _preprocess(self): # takes 5s
        # item, user 종류
        item_ids  = self.df['item'].unique()
        user_ids  = self.df['user'].unique()
        num_item, num_user = len(item_ids), len(user_ids)

        # user, item indexing
        item2idx = pd.Series(data=np.arange(len(item_ids))+1, index=item_ids) # item re-indexing (1~num_item)
        user2idx = pd.Series(data=np.arange(len(user_ids)), index=user_ids) # user re-indexing (0~num_user-1)

        # dataframe indexing - after: [time | item_idx | user_idx]
        self.df = pd.merge(self.df, pd.DataFrame({'item': item_ids, 'item_idx': item2idx[item_ids].values}), on='item', how='inner')
        self.df = pd.merge(self.df, pd.DataFrame({'user': user_ids, 'user_idx': user2idx[user_ids].values}), on='user', how='inner')
        self.df.sort_values(['user_idx', 'time'], inplace=True)
        del self.df['item'], self.df['user'] 
        return num_item, num_user, item2idx, user2idx
        
    def _split(self):
        """
        split to train set, valid set
        - train: 유저별 마지막 아이템 제외한 모든 아이템
        - valid: 유저별 마지막 아이템
        """
        users = defaultdict(list)
        for u, i, _ in zip(self.df['user_idx'], self.df['item_idx'], self.df['time']):
            users[u].append(i)
        user_train, user_valid = {}, {}
        for user in users:
            user_train[user] = users[user][:-1]
            user_valid[user] = [users[user][-1]]
        return user_train, user_valid

    def __len__(self):
        """학습에 사용할 sequence 개수"""
        return self.num_user

    def __getitem__(self, user): 
        user_seq = self.user_train[user]
        # 미리 max_len에 해당하는 array 생성, zero padding
        seq = np.zeros([self.max_len], dtype=np.int32)
        pos = np.zeros([self.max_len], dtype=np.int32)
        neg = np.zeros([self.max_len], dtype=np.int32)
        nxt = user_seq[-1]
        idx = self.max_len - 1
        # negative sample은 train sequence에 없는 item 사용
        for pos_sample in reversed(user_seq[:-1]):
            # 미리 정의된 sequence를 역순으로 채움, ex: seq = [0,0,0,1,2,3] (0은 pad)
            seq[idx] = pos_sample
            pos[idx] = nxt
            # padding 아닐 때
            if nxt != 0:
                neg[idx] = negative_sampling(self.num_item, user_seq)
            nxt = pos_sample
            idx -= 1
            if idx == -1: break
        return seq, pos, neg

#### utils

In [4]:
def negative_sampling(num_item, rated_item):
    neg_sample_item = np.random.randint(1, num_item+1)
    while neg_sample_item in rated_item:
        neg_sample_item = np.random.randint(1, num_item+1)
    return neg_sample_item

#### train/validate

In [5]:
def train(model, criterion, optimizer, data_loader):
    model.train()
    loss_val = 0
    for seq, pos, neg in data_loader:
        pos_logits, neg_logits = model(seq.cpu().numpy(), pos.cpu().numpy(), neg.cpu().numpy())
        pos_labels, neg_labels = torch.ones(pos_logits.shape, device=config.device), torch.zeros(neg_logits.shape, device=config.device)

        optimizer.zero_grad()
        indices = np.where(pos != 0)
        loss = criterion(pos_logits[indices], pos_labels[indices])
        loss += criterion(neg_logits[indices], neg_labels[indices])

        loss_val += loss.item()

        loss.backward()
        optimizer.step()
    
    loss_val /= len(data_loader)

    return loss_val

def validate(model, user_train, user_valid, max_len, num_user, num_item):
    model.eval()
    NDCG, HIT = 0.0, 0.0 # NDCG@10, HIT@10

    num_item_sample = 100
    num_user_sample = 1000
    users = np.random.randint(0, num_user, num_user_sample) # 1000개만 sampling 하여 evaluation
    
    for user in users:
        seq = user_train[user][-max_len:]
        rated = set(user_train[user] + user_valid[user])
        item_idx = user_valid[user] + [negative_sampling(num_item, rated) for _ in range(num_item_sample)]
        with torch.no_grad():
            predictions = -model.predict(np.array([seq]), np.array(item_idx))
            predictions = predictions[0]
            rank = predictions.argsort().argsort()[0].item()

        if rank < 10: # @10
            NDCG += 1 / np.log2(rank + 2)
            HIT += 1

    return NDCG/num_user_sample, HIT/num_user_sample

In [ ]:
import wandb

run_name = ""
for each in [config.max_len, config.batch_size, config.hidden_units, \
             config.num_heads, config.num_layers, config.dropout_rate, \
             config.lr, config.num_epochs]:
    run_name += "_" + str(each)

wandb.login()
wandb.init(project=f"SASRec", name=run_name, config=vars(config))

# settings
dataset = CustomDataset(config)
dataloader = DataLoader(dataset, batch_size=config.batch_size, shuffle=True, pin_memory=True, num_workers=config.num_workers)
model = SASRec(dataset.num_user, dataset.num_item, config.hidden_units, \
               config.num_heads, config.num_layers, config.max_len, \
               config.dropout_rate, config.device).to(config.device)
criterion = torch.nn.BCEWithLogitsLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=config.lr)

best_ndcg = 0
for epoch in range(1, config.num_epochs + 1):
    tbar = tqdm(range(1))
    for _ in tbar:
        loss = train(model=model, criterion=criterion, optimizer=optimizer, data_loader=dataloader)
        ndcg, hit = validate(model=model, user_train=dataset.user_train, user_valid=dataset.user_valid, \
                             max_len=config.max_len, num_user=dataset.num_user, num_item=dataset.num_item)

        # wandb log
        wandb.log({
                "epoch": epoch,
                "train_loss_epoch": loss,
                "valid_NDCG": ndcg,
                "valid_HIT": hit,
              })

        # save best model
        if best_ndcg < ndcg:
            best_ndcg = ndcg
            torch.save(model.state_dict(), os.path.join(config.model_path, config.model_name))

        tbar.set_description(f'Epoch: {epoch:3d}| Train loss: {loss:.5f}| NDCG@10: {ndcg:.5f}| HIT@10: {hit:.5f}')

wandb: WARNING Calling wandb.login() after wandb.init() has no effect.


Epoch:   1| Train loss: 3.86415| NDCG@10: 0.11858| HIT@10: 0.27700: 100%|██████████| 1/1 [00:06<00:00,  6.93s/it]
Epoch:   2| Train loss: 1.67411| NDCG@10: 0.26492| HIT@10: 0.51400: 100%|██████████| 1/1 [00:06<00:00,  6.90s/it]
Epoch:   3| Train loss: 1.16794| NDCG@10: 0.33461| HIT@10: 0.58000: 100%|██████████| 1/1 [00:06<00:00,  6.78s/it]
Epoch:   4| Train loss: 1.01840| NDCG@10: 0.34391| HIT@10: 0.57500: 100%|██████████| 1/1 [00:06<00:00,  6.92s/it]
Epoch:   5| Train loss: 0.95739| NDCG@10: 0.35431| HIT@10: 0.60000: 100%|██████████| 1/1 [00:06<00:00,  6.80s/it]
Epoch:   6| Train loss: 0.92349| NDCG@10: 0.33093| HIT@10: 0.57400: 100%|██████████| 1/1 [00:06<00:00,  6.93s/it]
Epoch:   7| Train loss: 0.90566| NDCG@10: 0.32355| HIT@10: 0.55900: 100%|██████████| 1/1 [00:07<00:00,  7.24s/it]
Epoch:   8| Train loss: 0.89585| NDCG@10: 0.35609| HIT@10: 0.61500: 100%|██████████| 1/1 [00:07<00:00,  7.35s/it]
Epoch:   9| Train loss: 0.89159| NDCG@10: 0.34289| HIT@10: 0.59400: 100%|██████████| 1/1

Epoch:   1| Train loss: 3.69329| NDCG@10: 0.12750| HIT@10: 0.29500: 100%|██████████| 1/1 [00:07<00:00,  7.15s/it]
Epoch:   2| Train loss: 1.53812| NDCG@10: 0.28186| HIT@10: 0.51700: 100%|██████████| 1/1 [00:07<00:00,  7.34s/it]
Epoch:   3| Train loss: 1.10509| NDCG@10: 0.33416| HIT@10: 0.57400: 100%|██████████| 1/1 [00:07<00:00,  7.14s/it]
Epoch:   4| Train loss: 0.99102| NDCG@10: 0.34863| HIT@10: 0.59300: 100%|██████████| 1/1 [00:07<00:00,  7.62s/it]
Epoch:   5| Train loss: 0.94692| NDCG@10: 0.35034| HIT@10: 0.60000: 100%|██████████| 1/1 [00:07<00:00,  7.10s/it]
Epoch:   6| Train loss: 0.92055| NDCG@10: 0.33776| HIT@10: 0.58200: 100%|██████████| 1/1 [00:07<00:00,  7.49s/it]
Epoch:   7| Train loss: 0.90449| NDCG@10: 0.34674| HIT@10: 0.58100: 100%|██████████| 1/1 [00:06<00:00,  6.92s/it]
Epoch:   8| Train loss: 0.89632| NDCG@10: 0.33948| HIT@10: 0.57500: 100%|██████████| 1/1 [00:06<00:00,  6.99s/it]
Epoch:   9| Train loss: 0.89251| NDCG@10: 0.35038| HIT@10: 0.59100: 100%|██████████| 1/1

Epoch:   1| Train loss: 3.47697| NDCG@10: 0.12326| HIT@10: 0.29700: 100%|██████████| 1/1 [00:07<00:00,  7.11s/it]
Epoch:   2| Train loss: 1.40468| NDCG@10: 0.28854| HIT@10: 0.54100: 100%|██████████| 1/1 [00:07<00:00,  7.06s/it]
Epoch:   3| Train loss: 1.04952| NDCG@10: 0.33875| HIT@10: 0.58700: 100%|██████████| 1/1 [00:07<00:00,  7.02s/it]
Epoch:   4| Train loss: 0.96946| NDCG@10: 0.35072| HIT@10: 0.59100: 100%|██████████| 1/1 [00:07<00:00,  7.09s/it]
Epoch:   5| Train loss: 0.93891| NDCG@10: 0.34082| HIT@10: 0.58200: 100%|██████████| 1/1 [00:07<00:00,  7.50s/it]
Epoch:   6| Train loss: 0.92074| NDCG@10: 0.32478| HIT@10: 0.56000: 100%|██████████| 1/1 [00:07<00:00,  7.29s/it]
Epoch:   7| Train loss: 0.91209| NDCG@10: 0.35004| HIT@10: 0.61100: 100%|██████████| 1/1 [00:07<00:00,  7.29s/it]
Epoch:   8| Train loss: 0.90451| NDCG@10: 0.35176| HIT@10: 0.59700: 100%|██████████| 1/1 [00:07<00:00,  7.21s/it]
Epoch:   9| Train loss: 0.89888| NDCG@10: 0.33767| HIT@10: 0.58600: 100%|██████████| 1/1

Epoch:   1| Train loss: 3.50267| NDCG@10: 0.10449| HIT@10: 0.25000: 100%|██████████| 1/1 [00:06<00:00,  6.79s/it]
Epoch:   2| Train loss: 1.37150| NDCG@10: 0.25766| HIT@10: 0.49300: 100%|██████████| 1/1 [00:06<00:00,  6.79s/it]
Epoch:   3| Train loss: 1.01633| NDCG@10: 0.33872| HIT@10: 0.57000: 100%|██████████| 1/1 [00:06<00:00,  6.82s/it]
Epoch:   4| Train loss: 0.94783| NDCG@10: 0.35031| HIT@10: 0.58700: 100%|██████████| 1/1 [00:06<00:00,  6.86s/it]
Epoch:   5| Train loss: 0.92769| NDCG@10: 0.34949| HIT@10: 0.59000: 100%|██████████| 1/1 [00:06<00:00,  6.86s/it]
Epoch:   6| Train loss: 0.91590| NDCG@10: 0.35008| HIT@10: 0.60600: 100%|██████████| 1/1 [00:07<00:00,  7.03s/it]
Epoch:   7| Train loss: 0.90907| NDCG@10: 0.33004| HIT@10: 0.58300: 100%|██████████| 1/1 [00:06<00:00,  6.88s/it]
Epoch:   8| Train loss: 0.90403| NDCG@10: 0.34030| HIT@10: 0.57500: 100%|██████████| 1/1 [00:06<00:00,  6.90s/it]
Epoch:   9| Train loss: 0.90097| NDCG@10: 0.35145| HIT@10: 0.60800: 100%|██████████| 1/1

...

Epoch:   1| Train loss: 4.04295| NDCG@10: 0.06555| HIT@10: 0.14000: 100%|██████████| 1/1 [00:14<00:00, 14.76s/it]
Epoch:   2| Train loss: 1.76707| NDCG@10: 0.17728| HIT@10: 0.41800: 100%|██████████| 1/1 [00:15<00:00, 15.56s/it]
Epoch:   3| Train loss: 1.09371| NDCG@10: 0.28058| HIT@10: 0.53600: 100%|██████████| 1/1 [00:15<00:00, 15.79s/it]
Epoch:   4| Train loss: 0.92535| NDCG@10: 0.32435| HIT@10: 0.58700: 100%|██████████| 1/1 [00:16<00:00, 16.02s/it]
Epoch:   5| Train loss: 0.89253| NDCG@10: 0.33542| HIT@10: 0.57500: 100%|██████████| 1/1 [00:16<00:00, 16.13s/it]
Epoch:   6| Train loss: 0.88616| NDCG@10: 0.34764| HIT@10: 0.58500: 100%|██████████| 1/1 [00:15<00:00, 15.20s/it]
Epoch:   7| Train loss: 0.88574| NDCG@10: 0.34842| HIT@10: 0.61200: 100%|██████████| 1/1 [00:13<00:00, 13.92s/it]
Epoch:   8| Train loss: 0.88671| NDCG@10: 0.34964| HIT@10: 0.60700: 100%|██████████| 1/1 [00:14<00:00, 14.40s/it]
Epoch:   9| Train loss: 0.88680| NDCG@10: 0.34602| HIT@10: 0.58100: 100%|██████████| 1/1

Epoch:  10| Train loss: 0.89811| NDCG@10: 0.34326| HIT@10: 0.58700: 100%|██████████| 1/1 [00:15<00:00, 15.85s/it]
wandb: WARNING Calling wandb.login() after wandb.init() has no effect.


Epoch:   3| Train loss: 1.21982| NDCG@10: 0.29224| HIT@10: 0.55500: 100%|██████████| 1/1 [00:18<00:00, 18.89s/it]
Epoch:   9| Train loss: 0.89922| NDCG@10: 0.34659| HIT@10: 0.57700: 100%|██████████| 1/1 [00:16<00:00, 16.06s/it]
Epoch:  10| Train loss: 0.89714| NDCG@10: 0.32893| HIT@10: 0.57700: 100%|██████████| 1/1 [00:16<00:00, 16.68s/it]
wandb: WARNING Calling wandb.login() after wandb.init() has no effect.


Epoch:   1| Train loss: 4.43453| NDCG@10: 0.08038| HIT@10: 0.18000: 100%|██████████| 1/1 [00:16<00:00, 16.79s/it]
Epoch:   2| Train loss: 1.98739| NDCG@10: 0.16253| HIT@10: 0.37200: 100%|██████████| 1/1 [00:17<00:00, 17.46s/it]
Epoch:   3| Train loss: 1.21687| NDCG@10: 0.30214| HIT@10: 0.55900: 100%|██████████| 1/1 [00:17<00:00, 17.64s/it]
Epoch:   4| Train loss: 1.00221| NDCG@10: 0.32594| HIT@10: 0.58100: 100%|██████████| 1/1 [00:18<00:00, 18.54s/it]
Epoch:   5| Train loss: 0.93867| NDCG@10: 0.34487| HIT@10: 0.58800: 100%|██████████| 1/1 [00:17<00:00, 17.64s/it]
Epoch:   6| Train loss: 0.91716| NDCG@10: 0.35231| HIT@10: 0.59600: 100%|██████████| 1/1 [00:17<00:00, 17.72s/it]
Epoch:   7| Train loss: 0.90831| NDCG@10: 0.35544| HIT@10: 0.61600: 100%|██████████| 1/1 [00:18<00:00, 18.38s/it]
Epoch:   8| Train loss: 0.90297| NDCG@10: 0.33961| HIT@10: 0.59000: 100%|██████████| 1/1 [00:17<00:00, 17.58s/it]
Epoch:   9| Train loss: 0.89924| NDCG@10: 0.33958| HIT@10: 0.57500: 100%|██████████| 1/1

Epoch:   4| Train loss: 1.28595| NDCG@10: 0.31152| HIT@10: 0.56000: 100%|██████████| 1/1 [00:12<00:00, 12.43s/it]
Epoch:   5| Train loss: 1.04372| NDCG@10: 0.32458| HIT@10: 0.57800: 100%|██████████| 1/1 [00:14<00:00, 14.01s/it]
Epoch:   6| Train loss: 1.00226| NDCG@10: 0.34879| HIT@10: 0.60600: 100%|██████████| 1/1 [00:12<00:00, 12.85s/it]
Epoch:   7| Train loss: 0.97549| NDCG@10: 0.35705| HIT@10: 0.61100: 100%|██████████| 1/1 [00:12<00:00, 12.45s/it]
Epoch:   9| Train loss: 0.91315| NDCG@10: 0.34265| HIT@10: 0.59400: 100%|██████████| 1/1 [00:14<00:00, 14.54s/it]
  0%|          | 0/1 [00:00<?, ?it/s]

#### inference

In [18]:
def inference(model, user_train, user_valid, num_user, max_len, item2idx, idx2item, idx2user):
    from time import time
    model.eval()
    u_list, i_list = list(), list()
    for u in tqdm(range(num_user)):
        seq = user_train[u][-max_len:]
        rated = set(user_train[u] + user_valid[u])
        item_idx = list(set(item2idx) - rated)
        with torch.no_grad():
            predictions = -model.predict(np.array([seq]), np.array(item_idx))
            predictions = predictions[0]
            rank10idx   = predictions.argsort()[:10].to('cpu').tolist()
            u_list.extend([idx2user[u]] * 10)
            for idx in rank10idx:
                i_list.append(idx2item[item_idx[idx]])

    submission_df = pd.DataFrame(zip(u_list, i_list), columns=['user','item'])
    submission_df.to_csv(f"SASRec-{str(time())[-5:]}.csv", index=False)

In [19]:
inference(model, dataset.user_train, dataset.user_valid, \
          dataset.num_user, config.max_len, dataset.item2idx, \
          dataset.idx2item, dataset.idx2user)

100%|██████████| 31360/31360 [02:03<00:00, 254.51it/s]
